In [3]:
import os
import json
from py2neo import Graph, Node

In [5]:
cur_dir = os.getcwd()

In [6]:
data_path = os.path.join(cur_dir, 'data/medical_rebuild.json')

In [7]:
g = Graph('bolt://10.1.50.194:7690', auth=("neo4j", "kt123456"),name='newdb')

In [11]:
# 共７类节点 每类内部节点不重复
drugs = []  # 药品
foods = []  # 食物
checks = []  # 检查
departments = []  # 科室
producers = []  # 药品大类
diseases = []  # 疾病
symptoms = []  # 症状

disease_infos = []  # 疾病信息

# 构建节点实体关系
rels_department = []  # 科室－科室关系 eg ['呼吸内科', '内科'] 小科室-大科室
rels_noteat = []  # 疾病－忌吃食物关系
rels_doeat = []  # 疾病－宜吃食物关系
rels_recommandeat = []  # 疾病－推荐吃食物关系
rels_commonddrug = []  # 疾病－通用药品关系
rels_recommanddrug = []  # 疾病－热门药品关系
rels_check = []  # 疾病－检查关系
rels_drug_producer = []  # 品牌药－药物名关系

rels_symptom = []  # 疾病症状关系
rels_acompany = []  # 疾病并发关系
rels_category = []  # 疾病所在的小科室 eg ['肺气肿', '呼吸内科'] 疾病-小科室

count = 0
for data in open(data_path):
    disease_dict = {}
    count += 1
    # print(count)
    data_json = json.loads(data)
    disease = data_json['name']
    disease_dict['name'] = disease
    diseases.append(disease)
    disease_dict['desc'] = ''
    disease_dict['prevent'] = ''
    disease_dict['cause'] = ''
    disease_dict['easy_get'] = ''
    disease_dict['cure_department'] = ''
    disease_dict['cure_way'] = ''
    disease_dict['cure_lasttime'] = ''
    disease_dict['symptom'] = ''
    disease_dict['cured_prob'] = ''

    if 'symptom' in data_json:
        symptoms += data_json['symptom']
        for symptom in data_json['symptom']:
            rels_symptom.append([disease, symptom])

    if 'acompany' in data_json:
        for acompany in data_json['acompany']:
            rels_acompany.append([disease, acompany])

    if 'desc' in data_json:
        disease_dict['desc'] = data_json['desc']

    if 'prevent' in data_json:
        disease_dict['prevent'] = data_json['prevent']

    if 'cause' in data_json:
        disease_dict['cause'] = data_json['cause']

    if 'get_prob' in data_json:
        disease_dict['get_prob'] = data_json['get_prob']

    if 'easy_get' in data_json:
        disease_dict['easy_get'] = data_json['easy_get']

    if 'cure_department' in data_json:
        cure_department = data_json['cure_department']
        if len(cure_department) == 1:
            rels_category.append([disease, cure_department[0]])
        if len(cure_department) == 2:
            big = cure_department[0]
            small = cure_department[1]
            rels_department.append([small, big])
            rels_category.append([disease, small])

        disease_dict['cure_department'] = cure_department
        departments += cure_department

    if 'cure_way' in data_json:
        disease_dict['cure_way'] = data_json['cure_way']

    if 'cure_lasttime' in data_json:
        disease_dict['cure_lasttime'] = data_json['cure_lasttime']

    if 'cured_prob' in data_json:
        disease_dict['cured_prob'] = data_json['cured_prob']

    if 'common_drug' in data_json:
        common_drug = data_json['common_drug']
        for drug in common_drug:
            rels_commonddrug.append([disease, drug])
        drugs += common_drug

    if 'recommand_drug' in data_json:
        recommand_drug = data_json['recommand_drug']
        drugs += recommand_drug
        for drug in recommand_drug:
            rels_recommanddrug.append([disease, drug])
    if 'not_eat' in data_json:
        not_eat = data_json['not_eat']
        for _not in not_eat:
            rels_noteat.append([disease, _not])

        foods += not_eat
        do_eat = data_json['do_eat']
        for _do in do_eat:
            rels_doeat.append([disease, _do])

        foods += do_eat
        recommand_eat = data_json['recommand_eat']

        for _recommand in recommand_eat:
            rels_recommandeat.append([disease, _recommand])
        foods += recommand_eat

    if 'check' in data_json:
        check = data_json['check']
        for _check in check:
            rels_check.append([disease, _check])
        checks += check
    if 'drug_detail' in data_json:
        drug_detail = data_json['drug_detail']
        producer = [i.split('(')[0] for i in drug_detail]
        rels_drug_producer += [[i.split('(')[0], i.split('(')[-1].replace(')', '')] for i in drug_detail]
        producers += producer
    disease_infos.append(disease_dict)

In [12]:
  disease_infos

[{'name': '肺泡蛋白质沉积症',
  'desc': '肺泡蛋白质沉积症(简称PAP)，又称Rosen-Castle-man-Liebow综合征，是一种罕见疾病。该病以肺泡和细支气管腔内充满PAS染色阳性，来自肺的富磷脂蛋白质物质为其特征，好发于青中年，男性发病约3倍于女性。',
  'prevent': '1、避免感染分支杆菌病，卡氏肺囊肿肺炎，巨细胞病毒等。\n2、注意锻炼身体，提高免疫力。',
  'cause': '病因未明，推测与几方面因素有关：如大量粉尘吸入（铝，二氧化硅等），机体免疫功能下降（尤其婴幼儿），遗传因素，酗酒，微生物感染等，而对于感染，有时很难确认是原发致病因素还是继发于肺泡蛋白沉着症，例如巨细胞病毒，卡氏肺孢子虫，组织胞浆菌感染等均发现有肺泡内高蛋白沉着。\n虽然启动因素尚不明确，但基本上同意发病过程为脂质代谢障碍所致，即由于机体内，外因素作用引起肺泡表面活性物质的代谢异常，到目前为止，研究较多的有肺泡巨噬细胞活力，动物实验证明巨噬细胞吞噬粉尘后其活力明显下降，而病员灌洗液中的巨噬细胞内颗粒可使正常细胞活力下降，经支气管肺泡灌洗治疗后，其肺泡巨噬细胞活力可上升，而研究未发现Ⅱ型细胞生成蛋白增加，全身脂代谢也无异常，因此目前一般认为本病与清除能力下降有关。',
  'easy_get': '',
  'cure_department': ['内科', '呼吸内科'],
  'cure_way': ['支气管肺泡灌洗'],
  'cure_lasttime': '约3个月',
  'symptom': '',
  'cured_prob': '约40%',
  'get_prob': '0.00002%'},
 {'name': '百日咳',
  'desc': '百日咳(pertussis，whoopingcough)是由百日咳杆菌所致的急性呼吸道传染病。其特征为阵发性痉挛性咳嗽，咳嗽末伴有特殊的鸡鸣样吸气吼声。病程较长，可达数周甚至3个月左右，故有百日咳之称。多见于5岁以下的小儿，幼婴患本病时易有窒息、肺炎，脑病等并发症，病死率高。百日咳患者，阴性感染者及带菌者为传染源。潜伏期末到病后2-3周传染性最强。百日咳经呼吸道飞沫传播。典型患者病程6-8周，临床病程可分3期：1.卡他期，从发病到开始出现咳嗽，一般1-2周。2,痉咳期，一

In [14]:
drugs

['穿心莲内酯片',
 '百咳静糖浆',
 '琥乙红霉素片',
 '琥乙红霉素颗粒',
 '百咳静糖浆',
 '穿心莲内酯片',
 '红霉素肠溶片',
 '环酯红霉素片',
 '布美他尼片',
 '十一味金色丸',
 '布美他尼片',
 '十一味金色丸',
 '注射用布美他尼',
 '注射用呋塞米',
 '盐酸利多卡因注射液',
 '注射用硫代硫酸钠',
 '大月晶丸',
 '仁青芒觉',
 '注射用鼠神经生长因子',
 '地塞米松磷酸钠注射液',
 '布地奈德气雾剂',
 '喷托维林氯化铵糖浆',
 '枸橼酸喷托维林片',
 '氨茶碱片',
 '二羟丙茶碱片',
 '胸腺肽肠溶片',
 '硫酸沙丁胺醇气雾剂',
 '小青龙合剂',
 '硫酸沙丁胺醇片',
 '蛇胆川贝液',
 '小青龙颗粒',
 '布地奈德气雾剂',
 '喷托维林氯化铵糖浆',
 '人血白蛋白',
 '注射用还原型谷胱甘肽钠',
 '注射用还原型谷胱甘肽钠',
 '注射用盐酸氨溴索',
 '人血白蛋白',
 '盐酸氨溴索葡萄糖注射液',
 '头孢泊肟酯胶囊',
 '头孢氨苄甲氧苄啶片',
 '注射用盐酸头孢替安',
 '注射用磺苄西林钠',
 '托西酸舒他西林胶囊',
 '头孢泊肟酯胶囊',
 '头孢氨苄甲氧苄啶片',
 '乳酸左氧氟沙星片',
 '阿奇霉素片',
 '阿奇霉素胶囊',
 '阿奇霉素分散片',
 '诺氟沙星胶囊',
 '阿奇霉素片',
 '乳酸左氧氟沙星片',
 '云南花粉片',
 '注射用盐酸溴己新',
 '注射用盐酸溴己新',
 '云南花粉片',
 '布美他尼片',
 '十一味金色丸',
 '布美他尼片',
 '十一味金色丸',
 '注射用布美他尼',
 '注射用呋塞米',
 '盐酸利多卡因注射液',
 '注射用硫代硫酸钠',
 '大月晶丸',
 '仁青芒觉',
 '注射用鼠神经生长因子',
 '地塞米松磷酸钠注射液',
 '甲硝唑片',
 '替硝唑片',
 '甲硝唑片',
 '甲硝唑维B6片',
 '替硝唑片',
 '奥硝唑片',
 '雷公藤多苷片',
 '甲泼尼龙片',
 '雷公藤多苷片',
 '注射用甲泼尼龙琥珀酸钠',
 '蒺藜药酒',
 '甲泼尼龙片',
 '盐酸克林霉素棕榈酸酯分散片',
 '盐酸克林霉素胶囊',
 '盐酸克林霉素棕榈酸酯分散片',
 '注射用美洛西

In [34]:
# 共７类节点 每类内部节点不重复
drugs = []  # 药品
foods = []  # 食物
checks = []  # 检查
departments = []  # 科室
producers = []  # 药品大类
diseases = []  # 疾病
symptoms = []  # 症状
hospitals = []
doctors = []
doctor_department_relations = []
department_hospital_relations = []
disease_infos = []  # 疾病信息

# 构建节点实体关系
rels_department = []  # 科室－科室关系 eg ['呼吸内科', '内科'] 小科室-大科室
rels_noteat = []  # 疾病－忌吃食物关系
rels_doeat = []  # 疾病－宜吃食物关系
rels_recommandeat = []  # 疾病－推荐吃食物关系
rels_commonddrug = []  # 疾病－通用药品关系
rels_recommanddrug = []  # 疾病－热门药品关系
rels_check = []  # 疾病－检查关系
rels_drug_producer = []  # 品牌药－药物名关系
rels_symptom = []  # 疾病症状关系
rels_acompany = []  # 疾病并发关系
rels_category = []  # 疾病所在的小科室 eg ['肺气肿', '呼吸内科'] 疾病-小科室


In [35]:
for data in open('/home/gujk/kg-QA/kg-app/medical_knowledge_graph_app-master-master/kg/data/hospital.json'):
            data_org = eval(data)
            for i in range(len(data_org)):
                data_json=data_org [i]
                if 'orgName' in data_json:
                    hospitals.append(data_json['orgName'])
                    doctors.append(data_json['empName'])
                    departments.append(data_json['ctDeptName'])
                    # Create relationships between doctors, departments, and hospitals
                    doctor_department_relations.append([data_json['empName'], data_json['ctDeptName']])
                    department_hospital_relations.append([data_json['ctDeptName'], data_json['orgName']])

In [36]:
set(hospitals)

{'宁波大学附属第一医院(宁波市第一医院）', '宁波市中医院', '宁波市妇女儿童医院', '宁波市第二医院'}

In [24]:
department_hospital_relations

[['口腔科', '宁波市第二医院'], ['口腔科', '宁波市第二医院']]

In [170]:
a={"_id": {"$oid": "5bb578da831b973a137e4e60"}, "name": "小儿慢性骨髓炎", "desc": "小儿慢性骨髓炎是化脓性细菌侵入骨组织所引起的一种骨感染性疾病，常反复发作多年不愈，有时会因并发症而致终身残疾。小儿慢性骨髓炎多由急性血源性骨髓炎治疗不当或延误诊治演变而来，少数为开放性骨折并发感染所致。机体抵抗力降低，病灶处可出现软组织红肿，甚或皮肤破溃，即急性发作。", "category": ["疾病百科", "儿科", "中医儿科"], "prevent": "一般感染性疾病的预防：疖、疔、疮、痈以及上呼吸道感染都是最常见的感染性疾病，且最易继发感染而致血源性骨髓炎的发生，因此预防疖、疮、痈及上呼吸道感染的发生，对预防骨髓炎的发生是十分重要的，其预防的主要措施是：\n1.保持室内气流通，注意环境卫生和个人卫生，保持皮肤清洁。\n2.青春期应多食蔬采水果，少用油剂润肤，以防止皮脂腺分泌物堆积或腺管阻塞。\n3.加强体育锻炼，增强身体素质，防止感冒发生。\n4.扁桃体炎反复发作者，应积极预防和治疗，必要时考虑手术摘除。\n(2)预防外伤感染：外伤感染包括组织损伤后感染和骨骼损伤后感染，也是引起骨髓炎的常见原因，因此，在日常生活中也应注意积极预防。", "cause": "发病前大都有一个未曾正确处理的化脓性感染病灶，如脓肿，疔痈，扁桃体炎等，细菌通过血液循环被带到骨组织而发生骨髓炎，是最常见的，最主要的感染途径，在临床上，由血源性感染途径而发生的骨髓炎称为血源性骨髓炎。\n如刀伤，弹伤，开放性骨折或闭合性骨折，或关节手术时无菌操作不严等情况，病原菌直接由伤口侵入骨组织，引起骨髓炎临床上称为创伤性骨髓炎。\n直接由邻近的化脓病灶蔓延到骨组织而引起骨髓炎，如指(趾)端感染引起的指(趾)骨髓炎，临床上称为感染性骨髓炎。感染途径以血源性骨髓炎发病率最高，其发病部位，多在长管骨，尤其是下肢骨，如胫骨上端，股骨下端，其发病率由高到低的顺序为：胫骨，股骨，肱骨，桡骨，髂骨，脊椎骨等。\n发病机制\n一般将急性骨髓炎经过3周以上的治疗尚未痊愈，或急性炎症消退后，出现死骨，窦道者则转为慢性骨髓炎。\n其病理改变比较复杂，包括死骨，新生骨形成的包壳，死骨周围有大量炎性肉芽组织和脓液，当脓液向软组织扩散，使皮肤破溃形成窦道，排出脓液和小块死骨之后，急性炎症可逐渐消退，窦道口便暂时", "symptom": ["畏寒", "食欲减退", "死骨", "肌肉萎缩"], "yibao_status": "否", "get_prob": "0.001%", "easy_get": "儿童", "get_way": "无传染性", "acompany": ["肌肉萎缩"], "cure_department": ["儿科", "中医儿科"], "cure_way": ["手术治疗", "药物治疗", "支持治疗"], "cure_lasttime": "10-30天", "cured_prob": "70%", "common_drug": ["盐酸左氧氟沙星胶囊", "乳酸左氧氟沙星片"], "cost_money": "根据不同医院，收费标准不一致，市三甲医院约（10000——50000元）", "check": ["血液及骨髓细菌培养", "脊椎平片", "骨显像", "四肢的骨和关节平片", "全身骨骼疾病排查", "血常规", "直接涂片检查"], "do_eat": ["芝麻", "南瓜子仁", "绿豆", "黄豆粉"], "not_eat": ["白砂糖", "花生（炒）", "白扁豆", "螃蟹"], "recommand_eat": ["肉末胡萝卜炒饭", "青胡萝卜排骨汤", "红萝卜鲜木耳豆腐汤", "黑木耳大枣汤", "黑豆蛋粥", "荠菜黑豆粥", "绿豆荷叶粥", "绿豆粥"], "recommand_drug": ["替硝唑胶囊", "盐酸米诺环素胶囊", "盐酸克林霉素棕榈酸酯干混悬剂", "盐酸环丙沙星片", "丹参酮胶囊", "盐酸左氧氟沙星胶囊", "盐酸左氧氟沙星分散片", "4:1分散片", "替硝唑片", "注射用头孢曲松钠", "盐酸克林霉素胶囊", "阿莫西林双氯西林钠胶囊", "骨炎灵片", "盐酸克林霉素棕榈酸酯分散片", "八味秦皮丸", "氧氟沙星片", "乳酸左氧氟沙星片"], "drug_detail": ["联邦左福康盐酸左氧氟沙星胶(盐酸左氧氟沙星胶囊)", "佳乐弗乳酸左氧氟沙星片(乳酸左氧氟沙星片)", "安徽新世纪盐酸左氧氟沙星胶(盐酸左氧氟沙星胶囊)", "博美欣(阿莫西林克拉维酸钾(4:1)分散片)", "四川大冢盐酸左氧氟沙星胶囊(盐酸左氧氟沙星胶囊)", "浙江得恩德氧氟沙星片(氧氟沙星片)", "凯莱克林盐酸克林霉素棕榈酸(盐酸克林霉素棕榈酸酯分散片)", "泰利必妥(氧氟沙星片)", "遂成药业替硝唑胶囊(替硝唑胶囊)", "康尼(盐酸米诺环素胶囊)", "丽珠集团替硝唑片(替硝唑片)", "宁新宝盐酸左氧氟沙星胶囊(盐酸左氧氟沙星胶囊)", "泉盈(盐酸左氧氟沙星分散片)", "罗氏芬(注射用头孢曲松钠)", "舍悦(盐酸克林霉素棕榈酸酯干混悬剂)", "吉林通化博祥骨炎灵片(骨炎灵片)", "甘露八味秦皮丸(八味秦皮丸)", "深圳海王盐酸克林霉素胶囊(盐酸克林霉素胶囊)", "澳广(阿莫西林双氯西林钠胶囊)", "希力丹参酮胶囊(丹参酮胶囊)", "山西津华晖星盐酸环丙沙星片(盐酸环丙沙星片)", "莱阳江波盐酸环丙沙星片(盐酸环丙沙星片)", "民生盐酸克林霉素胶囊(盐酸克林霉素胶囊)"]}


In [203]:
a['cause']

'发病前大都有一个未曾正确处理的化脓性感染病灶，如脓肿，疔痈，扁桃体炎等，细菌通过血液循环被带到骨组织而发生骨髓炎，是最常见的，最主要的感染途径，在临床上，由血源性感染途径而发生的骨髓炎称为血源性骨髓炎。\n如刀伤，弹伤，开放性骨折或闭合性骨折，或关节手术时无菌操作不严等情况，病原菌直接由伤口侵入骨组织，引起骨髓炎临床上称为创伤性骨髓炎。\n直接由邻近的化脓病灶蔓延到骨组织而引起骨髓炎，如指(趾)端感染引起的指(趾)骨髓炎，临床上称为感染性骨髓炎。感染途径以血源性骨髓炎发病率最高，其发病部位，多在长管骨，尤其是下肢骨，如胫骨上端，股骨下端，其发病率由高到低的顺序为：胫骨，股骨，肱骨，桡骨，髂骨，脊椎骨等。\n发病机制\n一般将急性骨髓炎经过3周以上的治疗尚未痊愈，或急性炎症消退后，出现死骨，窦道者则转为慢性骨髓炎。\n其病理改变比较复杂，包括死骨，新生骨形成的包壳，死骨周围有大量炎性肉芽组织和脓液，当脓液向软组织扩散，使皮肤破溃形成窦道，排出脓液和小块死骨之后，急性炎症可逐渐消退，窦道口便暂时'

In [178]:
for i in a.keys():
    print('dict_info[\''+i+'\']')

dict_info['_id']
dict_info['name']
dict_info['desc']
dict_info['category']
dict_info['prevent']
dict_info['cause']
dict_info['symptom']
dict_info['yibao_status']
dict_info['get_prob']
dict_info['easy_get']
dict_info['get_way']
dict_info['acompany']
dict_info['cure_department']
dict_info['cure_way']
dict_info['cure_lasttime']
dict_info['cured_prob']
dict_info['common_drug']
dict_info['cost_money']
dict_info['check']
dict_info['do_eat']
dict_info['not_eat']
dict_info['recommand_eat']
dict_info['recommand_drug']
dict_info['drug_detail']


In [10]:
import requests
from lxml import html
from denycheck import deny_check
num=10031


In [32]:

def spider_up(num):
    dict_info={}
    cookies = {
        'clientac': '1699405066692956126',
        'visit_dt': '2023-10-8',
        '_ga': 'GA1.2.1001444342.1699405067',
        '_gid': 'GA1.2.217938350.1699405067',
        '_ga_0J18S6XWJY': 'GS1.2.1699405067.1.0.1699405067.0.0.0',
        'Hm_lvt_f954228be9b5d93a74a625d18203e150': '1699404948,1699405086',
        'Hm_lpvt_f954228be9b5d93a74a625d18203e150': '1699405086',
        'bush-20480-tech-M-web-release-01': 'NDACBOAKFAAA',
        'Hm_lvt_df6ae9f94a8364bb76ee4b2d30eff681': '1699405269',
        'xywylastUrl': 'http%253A%252F%252Fjib.xywy.com%252Fil_sii%252Fgaishu%252F10122.htm',
        'xywylastRef': 'http%253A%252F%252Fjib.xywy.com%252Fil_sii_10122.htm',
        'ajsDataSession': '1699405066692330512@30@1699405370@1',
        'tj_lastUrl': 'http%3A//jib.xywy.com/il_sii/gaishu/10122.htm',
        'tj_lastUrl_time': '1699405370865',
        'ajsDataSession_js_test': '16994052693247911141@4@1699405370@1@http%253A%252F%252Fjib.xywy.com%252Fil_sii%252Fgaishu%252F10122.htm@http%253A%252F%252Fjib.xywy.com%252Fil_sii_10122.htm',
        'tj_lastUrl_js_test': 'http%3A//jib.xywy.com/il_sii/gaishu/10122.htm',
        'tj_lastUrl_js_test_time': '1699405370951',
        'Hm_lpvt_df6ae9f94a8364bb76ee4b2d30eff681': '1699405371',
    }
    headers = {
        'Accept': 'text/html,application/xhtml+xml,application/xml;q=0.9,image/webp,image/apng,*/*;q=0.8,application/signed-exchange;v=b3;q=0.7',
        'Accept-Language': 'zh-CN,zh;q=0.9,en;q=0.8,en-US;q=0.7,ko;q=0.6,en-GB;q=0.5',
        'Cache-Control': 'max-age=0',
        # 'Cookie': 'clientac=1699405066692956126; visit_dt=2023-10-8; _ga=GA1.2.1001444342.1699405067; _gid=GA1.2.217938350.1699405067; _ga_0J18S6XWJY=GS1.2.1699405067.1.0.1699405067.0.0.0; Hm_lvt_f954228be9b5d93a74a625d18203e150=1699404948,1699405086; Hm_lpvt_f954228be9b5d93a74a625d18203e150=1699405086; bush-20480-tech-M-web-release-01=NDACBOAKFAAA; Hm_lvt_df6ae9f94a8364bb76ee4b2d30eff681=1699405269; xywylastUrl=http%253A%252F%252Fjib.xywy.com%252Fil_sii%252Fgaishu%252F10122.htm; xywylastRef=http%253A%252F%252Fjib.xywy.com%252Fil_sii_10122.htm; ajsDataSession=1699405066692330512@30@1699405370@1; tj_lastUrl=http%3A//jib.xywy.com/il_sii/gaishu/10122.htm; tj_lastUrl_time=1699405370865; ajsDataSession_js_test=16994052693247911141@4@1699405370@1@http%253A%252F%252Fjib.xywy.com%252Fil_sii%252Fgaishu%252F10122.htm@http%253A%252F%252Fjib.xywy.com%252Fil_sii_10122.htm; tj_lastUrl_js_test=http%3A//jib.xywy.com/il_sii/gaishu/10122.htm; tj_lastUrl_js_test_time=1699405370951; Hm_lpvt_df6ae9f94a8364bb76ee4b2d30eff681=1699405371',
        'Proxy-Connection': 'keep-alive',
        'Referer': 'http://jib.xywy.com/il_sii_10122.htm',
        'Upgrade-Insecure-Requests': '1',
        'User-Agent': 'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_7) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/119.0.0.0 Safari/537.36 Edg/119.0.0.0',
    }
    dict_info['_id']={"$oid": f"5bb578da831b973a137e4{num}"}
    response = requests.get(f'http://jib.xywy.com/il_sii/gaishu/{num}.htm', cookies=cookies, headers=headers, verify=False)
    etree = html.etree
    etree_html = etree.HTML(response.text)
    dict_info['name']=''.join(etree_html.xpath('/html/body/div[5]/div/text()'))
    dict_info['desc']=''.join(etree_html.xpath('/html/body/div[6]/div[1]/div[1]/div[2]/div[1]/p/text()'))
    dict_info['cure_department']=''.join(etree_html.xpath('/html/body/div[6]/div[1]/div[1]/div[2]/div[3]/p[1]/span[2]/text()')).split()
    common_drug=[]
    cata=[]
    for i in range(1,10):
        cata+=etree_html.xpath(f'/html/body/div[4]/a[{i}]/text()')
    dict_info['category']=cata
    for i in range(1,20):
        common_drug+=etree_html.xpath(f'/html/body/div[6]/div[1]/div[1]/div[2]/div[3]/p[5]/span[2]/a[{i}]/text()')
    dict_info['common_drug']=common_drug
    dict_info['yibao_status']=''.join(etree_html.xpath('/html/body/div[6]/div[1]/div[1]/div[2]/div[2]/p[1]/span[2]/text()')).replace('\n','').replace(' ','')
    dict_info['get_prob']=''.join(etree_html.xpath('/html/body/div[6]/div[1]/div[1]/div[2]/div[2]/p[2]/span[2]/text()')).replace('\n','').replace(' ','')
    dict_info['easy_get']=''.join(etree_html.xpath('/html/body/div[6]/div[1]/div[1]/div[2]/div[2]/p[3]/span[2]/text()')).replace('\n','').replace(' ','')
    dict_info['get_way']= ''.join(etree_html.xpath('/html/body/div[6]/div[1]/div[1]/div[2]/div[2]/p[4]/span[2]/text()'))
    acompany=[]
    for i in range(1,20):
        acompany+=etree_html.xpath(f'/html/body/div[6]/div[1]/div[1]/div[2]/div[2]/p[5]/span[2]/a[{i}]/text()')
    dict_info['acompany']=acompany
    dict_info['cure_way']=''.join(etree_html.xpath('/html/body/div[6]/div[1]/div[1]/div[2]/div[3]/p[2]/span[2]/text()')).replace('\n','').split()
    dict_info['cure_lasttime']=''.join(etree_html.xpath('/html/body/div[6]/div[1]/div[1]/div[2]/div[3]/p[3]/span[2]/text()')).replace('\n','').replace(' ','')
    dict_info['cured_prob']=''.join(etree_html.xpath('/html/body/div[6]/div[1]/div[1]/div[2]/div[3]/p[4]/span[2]/text()')).replace('\n','').replace(' ','')
    dict_info['cost_money']=''.join(etree_html.xpath('/html/body/div[6]/div[1]/div[1]/div[2]/div[3]/p[6]/span[2]/text()'))
    response2 = requests.get(f'http://jib.xywy.com/il_sii/symptom/{num}.htm', cookies=cookies, headers=headers, verify=False)
    etree2 = html.etree
    etree_html2 = etree2.HTML(response2.text)
    dict_info['symptom']=deny_check(''.join(etree_html2.xpath('/html/body/div[6]/div[1]/div[1]/div[2]/p/text()')).replace('\n','').replace('\t','').replace('\r','').replace('。','').split('、')).split('、')
    response3 = requests.get(f'http://jib.xywy.com/il_sii/food/{num}.htm', cookies=cookies, headers=headers, verify=False)
    etree3 = html.etree
    etree_html3 = etree3.HTML(response3.text)
    do_eat=[]
    for i in range(1,20):
        do_eat+=etree_html3.xpath(f'/html/body/div[6]/div[1]/div[1]/div[2]/div/div[2]/div[2]/div[2]/div[{i}]/p/text()')
    dict_info['do_eat']=do_eat
    do_not_eat=[]
    for i in range(1,20):
        do_not_eat+=etree_html3.xpath(f'/html/body/div[6]/div[1]/div[1]/div[2]/div/div[2]/div[3]/div[2]/div[{i}]/p/text()')
    dict_info['not_eat']=do_not_eat
    recommand_eat=[]
    for i in range(1,20):
        recommand_eat+=etree_html3.xpath(f'/html/body/div[6]/div[1]/div[1]/div[2]/div/div[2]/div[4]/div[{i}]/div[1]/p/text()')
    dict_info['recommand_eat']=recommand_eat
    response4 = requests.get(f'http://jib.xywy.com/il_sii/prevent/{num}.htm', cookies=cookies, headers=headers, verify=False)
    etree4 = html.etree
    etree_html4 = etree4.HTML(response4.text)

    dict_info['prevent'] = ''.join(etree_html4.xpath('/html/body/div[6]/div[1]/div[1]/div[2]/p/text()')) 
    response5 = requests.get(f'http://jib.xywy.com/il_sii/drug/{num}.htm', cookies=cookies, headers=headers, verify=False)
    etree5 = html.etree
    etree_html5 = etree5.HTML(response5.text)
    drug_detail=[]
    for i in range(1,100):
        drug_detail+=etree_html5.xpath(f'/html/body/div[6]/div[1]/div/div/div/div[{i}]/div[2]/p[1]/a/text()')
    dict_info['drug_detail']= [text.replace(' ','').replace('\n','') for text in drug_detail]
    dict_info['check']=[]
    dict_info['recommand_drug']=common_drug
    response6 = requests.get(f'http://jib.xywy.com/il_sii/cause/{num}.htm', cookies=cookies, headers=headers, verify=False)
    etree6 = html.etree
    etree_html6 = etree6.HTML(response6.text)
    dict_info['cause']=''.join(etree_html6.xpath(f'/html/body/div[6]/div[1]/div[1]/div[2]/p/text()'))
    return dict_info

In [33]:
dict_info=spider_up(169)

In [35]:
 print(dict_info)

{'_id': {'$oid': '5bb578da831b973a137e4169'}, 'name': '高血压', 'desc': '\r\n\t高血压是以体循环动脉压增高为主要表现的临床综合征，是最常见的心血管疾病，长期高血压，还是多种心血管疾病的重要危险因素，并影响重要器官如心，脑，肾的功能，最终导致这些器官的功能衰竭，可分为原发性及继发性两大类，在大多数患者中，高血压的病因不明，称之为原发性高血压，占总高血压患者95%以上，在不足5%的患者中，血压升高是某些疾病的一种临床表现，本身有明确而独立的疾病，称为继发性高血压。目前我国采用国际上统一的诊断标准，即收缩压大于或等于140毫米汞柱和(或)舒张压大于或等于九十毫米汞柱，即诊断为高血压。收缩压≥140mmHg和舒张压<90mmHg，单列为单纯性收缩期高血压。可进一步分为高血压，1，2，3级，结合患者总的心血管疾病危险因素及合并的靶器官损害，分为低危，中危，高危。\r\n\n\n                    ', 'cure_department': ['内科', '心内科'], 'category': ['疾病百科', '内科', '心内科'], 'common_drug': ['盐酸贝那普利片', '缬沙坦胶囊'], 'yibao_status': '否', 'get_prob': '15.8%', 'easy_get': '有高血压家族史，不良的生活习惯，缺乏运动的人群', 'get_way': '非传染性疾病', 'acompany': ['冠心病', '高血压脑病', '高血压危象', '中风'], 'cure_way': ['药物治疗', '手术治疗', '支持性治疗'], 'cure_lasttime': '1-3个月', 'cured_prob': '0.0001%(终身性疾病)', 'cost_money': '根据不同医院，所选用药物不同，收费标准不一致，市三甲医院约（2000-10000元）', 'symptom': ['呕吐', '后期', '头痛', '动脉硬化', '精神紧张', '视神经乳头水肿', '高血压危象', '疲劳', '脑病', '昏迷', '失语', '夜尿', '多尿', '心功能', '抽搐', '耳鸣', '失眠', '肾功能不全', '偏瘫', 

In [138]:
cookies = {
    'clientac': '1699405066692956126',
    'visit_dt': '2023-10-8',
    '_ga': 'GA1.2.1001444342.1699405067',
    '_gid': 'GA1.2.217938350.1699405067',
    '_ga_0J18S6XWJY': 'GS1.2.1699405067.1.0.1699405067.0.0.0',
    'Hm_lvt_f954228be9b5d93a74a625d18203e150': '1699404948,1699405086',
    'Hm_lpvt_f954228be9b5d93a74a625d18203e150': '1699405086',
    'bush-20480-tech-M-web-release-01': 'NDACBOAKFAAA',
    'Hm_lvt_df6ae9f94a8364bb76ee4b2d30eff681': '1699405269',
    'xywylastUrl': 'http%253A%252F%252Fjib.xywy.com%252Fil_sii%252Fgaishu%252F10122.htm',
    'xywylastRef': 'http%253A%252F%252Fjib.xywy.com%252Fil_sii_10122.htm',
    'ajsDataSession': '1699405066692330512@30@1699405370@1',
    'tj_lastUrl': 'http%3A//jib.xywy.com/il_sii/gaishu/10122.htm',
    'tj_lastUrl_time': '1699405370865',
    'ajsDataSession_js_test': '16994052693247911141@4@1699405370@1@http%253A%252F%252Fjib.xywy.com%252Fil_sii%252Fgaishu%252F10122.htm@http%253A%252F%252Fjib.xywy.com%252Fil_sii_10122.htm',
    'tj_lastUrl_js_test': 'http%3A//jib.xywy.com/il_sii/gaishu/10122.htm',
    'tj_lastUrl_js_test_time': '1699405370951',
    'Hm_lpvt_df6ae9f94a8364bb76ee4b2d30eff681': '1699405371',
}
headers = {
    'Accept': 'text/html,application/xhtml+xml,application/xml;q=0.9,image/webp,image/apng,*/*;q=0.8,application/signed-exchange;v=b3;q=0.7',
    'Accept-Language': 'zh-CN,zh;q=0.9,en;q=0.8,en-US;q=0.7,ko;q=0.6,en-GB;q=0.5',
    'Cache-Control': 'max-age=0',
    # 'Cookie': 'clientac=1699405066692956126; visit_dt=2023-10-8; _ga=GA1.2.1001444342.1699405067; _gid=GA1.2.217938350.1699405067; _ga_0J18S6XWJY=GS1.2.1699405067.1.0.1699405067.0.0.0; Hm_lvt_f954228be9b5d93a74a625d18203e150=1699404948,1699405086; Hm_lpvt_f954228be9b5d93a74a625d18203e150=1699405086; bush-20480-tech-M-web-release-01=NDACBOAKFAAA; Hm_lvt_df6ae9f94a8364bb76ee4b2d30eff681=1699405269; xywylastUrl=http%253A%252F%252Fjib.xywy.com%252Fil_sii%252Fgaishu%252F10122.htm; xywylastRef=http%253A%252F%252Fjib.xywy.com%252Fil_sii_10122.htm; ajsDataSession=1699405066692330512@30@1699405370@1; tj_lastUrl=http%3A//jib.xywy.com/il_sii/gaishu/10122.htm; tj_lastUrl_time=1699405370865; ajsDataSession_js_test=16994052693247911141@4@1699405370@1@http%253A%252F%252Fjib.xywy.com%252Fil_sii%252Fgaishu%252F10122.htm@http%253A%252F%252Fjib.xywy.com%252Fil_sii_10122.htm; tj_lastUrl_js_test=http%3A//jib.xywy.com/il_sii/gaishu/10122.htm; tj_lastUrl_js_test_time=1699405370951; Hm_lpvt_df6ae9f94a8364bb76ee4b2d30eff681=1699405371',
    'Proxy-Connection': 'keep-alive',
    'Referer': 'http://jib.xywy.com/il_sii_10122.htm',
    'Upgrade-Insecure-Requests': '1',
    'User-Agent': 'Mozilla/5.0 (Macintosh; Intel Mac OS X 10_15_7) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/119.0.0.0 Safari/537.36 Edg/119.0.0.0',
}
response6 = requests.get(f'http://jib.xywy.com/html/l.html', cookies=cookies, headers=headers, verify=False)
response6.encoding = 'gbk'
etree6 = html.etree
etree_html6 = etree6.HTML(response6.text)

In [139]:
import re

In [142]:
print(response6.text)

<!DOCTYPE html PUBLIC "-//W3C//DTD XHTML 1.0 Transitional//EN" "http://www.w3.org/TR/xhtml1/DTD/xhtml1-transitional.dtd">
<html xmlns="http://www.w3.org/1999/xhtml">
<head>
    <meta http-equiv="Content-Type" content="text/html; charset=gb2312" />
        <meta http-equiv="mobile-agent" content="format=xhtml; url=http://3g.jib.xywy.com/zmcx_L.htm">
        





<title>按字母L找疾病-疾病查询-寻医问药-xywy.com</title>
<meta name="keywords" content="按字母B找疾病, 字母B疾病列表" />
<meta name="description" content="寻医问药闻康网疾病频道按字母B找疾病列表，为您提供方便的按字母查询疾病，字母B开头的疾病，字母B开头的常见疾病查询。"/>

    <link type="text/css" rel="stylesheet" href="//static.wkimg.com/common/ui/base/reset.css" />
    <link rel="stylesheet" type="text/css" href="//css.static.xywy.com/jbindex/css/main.css" />
    <link rel="stylesheet" type="text/css" href="//pub1.wkimg.com/common_login/css/common_login_v2.css" />
    <script type="text/javascript" src="//static.wkimg.com/common/lib/jquery.min.js"></script>
	<!--<script type="text/javascript" src="//ipdisp

In [140]:
def extract_numbers(text):
    pattern = r'\d+'  # 匹配连续的数字
    numbers = re.findall(pattern, text)
    return numbers


In [155]:
ds=[]
for i in range(1,100):
    a=etree_html6.xpath(f'/html/body/div[5]/div/div[1]/div[1]/ul/li[{i}]/a/text()')
    if len(a)>0:
        for p in a:
            ds.append(p)

In [156]:
ds

[' 肋软骨炎',
 ' 痢疾',
 ' 老年人糖尿病',
 ' 黧黑斑',
 ' 淋巴结核',
 ' 卵巢功能异常综合征',
 ' 裂纹舌',
 ' 卵巢黄体囊肿破裂',
 ' 瘰疬',
 ' 淋巴病',
 ' 卵巢性不孕',
 ' 流行性脑脊髓膜炎',
 ' 卵巢宫内膜样肿瘤',
 ' 老年人肾病综合征']

In [137]:
for i in ds:
    print(spider_up(int(i)))

{'_id': {'$oid': '5bb578da831b973a137e44817'}, 'name': '阿尔茨海默病性痴呆', 'desc': '\r\n\t阿尔茨海默病性痴呆(dementia in Alzheimer’s disease，AD)是一种起病隐袭的发生于老年和老年前期、以进行性发展的认知功能障碍和行为损害为特征的神经系统退行性疾病，临床上以记忆障碍，失语、失用、失认，视空间技能损害、执行功能障碍以及人格和行为改变等全面性痴呆表现为特征，病因迄今未明。过去将65岁以前发病者，称早老性痴呆(presenile dementia);65岁以后发病者称老年性痴呆(senile dementia)。本病病理改变主要特征为大脑皮质萎缩、神经原纤维化和脑神经细胞变性及老年斑，是老年期常见的痴呆类型，约占老年期痴呆的50%-70%，我国目前AD患者约600万-800万。\r\n\n\n                    ', 'cure_department': ['精神科'], 'category': ['疾病百科', '精神科'], 'common_drug': ['奥拉西坦胶囊', '尼麦角林片'], 'yibao_status': '否', 'get_prob': '老年人患病概率3-7%', 'easy_get': '好发于老年人', 'get_way': '无传染性', 'acompany': ['老年人血管性痴呆', '血管性痴呆', '麻痹性痴呆'], 'cure_way': ['药物治疗', '综合性治疗和护理'], 'cure_lasttime': '需要终身治疗', 'cured_prob': '需要终身治疗，目前不能治愈', 'cost_money': '根据不同医院，收费标准不一致', 'symptom': ['失认', '贫困', '肿瘤', '幻视', '言语困难', '感觉性失语', '谵妄', '色素沉着', '癫痫样发作', '中期', '言语障碍', '失语', '认知障碍', '命名性失语', '感染', '老年性谵妄', '行为异常', '遗忘', '观察', '幻觉', '手淫', '综合征', '急躁', '精神错乱', '脑血管病', '痴呆', '淡漠', '发病', '认识不能', '晚期', '迟钝'

In [116]:
print(spider_up(3676))

{'_id': {'$oid': '5bb578da831b973a137e43676'}, 'name': '放射病', 'desc': '急性放射病(acute radiation \ndisease)是机体在短时间内受到大剂量(>1Gy)电离辐射照射引起的全身性疾病，外照射和内照射都可能发生急性放射病，但以外照射为主。外照射引起急性放射病的射线有γ线，中子和X射线等。放射性工作者应严格遵守操作规程和防护规定，以减少不必要的照射，辐射源与工作人员之间应按射线性质安置屏蔽物;操作要熟练，缩短接触放射源的时间;设法增加与放射源之间的距离，以减少照射剂量，应进行严格的就业前体检，活动性肺结核，糖尿病，肾小球肾炎，内分泌及血液系统疾病，均属接触射线的禁忌证，定期体格检查，建立个人健康和剂量档案资料，使用放射源时应设置醒目标志，以防意外。\n\n                    ', 'cure_department': ['肿瘤科', '肿瘤内科'], 'category': ['疾病百科', '肿瘤科', '肿瘤内科'], 'common_drug': ['唐草片', '马来酸氯苯那敏片'], 'yibao_status': '否', 'get_prob': '0.0325%', 'easy_get': '无特殊人群', 'get_way': '无传染性', 'acompany': ['肠套叠', '肠梗阻'], 'cure_way': ['对症治疗', '药物治疗', '支持治疗'], 'cure_lasttime': '约4-8周', 'cured_prob': '治愈率30-40%', 'cost_money': '根据不同医院，收费标准不一致，市三甲医院约（5000——10000元）', 'symptom': ['初期', '震颤', '呕吐', '腹痛', '共济失调', '乏力', '放射病', '不适', '恶心', '腹泻', '休克'], 'do_eat': ['蜂蜜', '鸭翅', '芝麻', '腰果'], 'not_eat': ['啤酒', '白酒', '鸡蛋黄', '赤小豆'], 'recommand_eat': ['海带瘦肉粥'], 'prevent': '\n\t放射性工作者应严格遵守操作规程和防护规定，以减少不必要的照射，辐射源与工

In [ ]:
a={"_id": {"$oid": "5bb578bd831b973a137e412c"}, "name": "原发性肝癌", "desc": "原发性肝癌(primarycarcinomaoftheliver)是我国常见恶性肿瘤之一，死亡率在消化系统恶性肿瘤中列第3位.我国每年死于肝癌约11万人，占全世界肝癌死亡人数的45%。由于依靠血清甲胎蛋白(AFP)检测结合超声显像对高危人群的监测，使肝癌在亚临床阶段即可和出诊断，早期切除的远期效果尤为显著。加之积极综合治疗，已便肝癌的五年生存率有了显著提高。本病可发生于任何年龄，以40～49岁最多，男女之比为2～5∶1。", "category": ["疾病百科", "肿瘤科", "中医肿瘤科"], "prevent": "肝癌的日常预防\n积极防治病毒性肝炎，对降低肝癌发病率有重要意义。乙肝病毒灭活疫苗预防注射不仅防治肝炎有效果，对肝癌预防也必将起一定作用。避免不必要的输血和应用血制品。预防粮食霉变、改进饮水水质，戒除饮酒嗜好亦是预防肝癌的重要措施。在肝癌的一级预防尚未完善之际，肝癌的早期发现、早期诊断、早期治疗在肿瘤学上被称为“二级预防”则显得十分重要。自实施肝癌筛查以来，原发性肝癌的诊断进入了亚临床水平，早期肝癌比例不断增高，5年生存率亦明显提高。20世纪80年代以来对肝癌的高危对象(35岁以上有慢性肝炎史或HBsAg阳性者)采用检测AFP与超声进行筛查，检出了许多早期肝癌，经过早期诊断、早期治疗，有效地降低了肝癌的病死率。\n肝癌的健康教育\n肝癌是我国最常见的恶性肿瘤之一，每年新发病例约11万例，占全世界病例40%左右。控制肝癌的发病率、降低死亡率，目前肝癌防治已列入我国预防重点。肝癌的人群预防以一级预防和人口普查或筛检为重点。\n一、肝癌的一级预防\n是指以预防肝癌的发生为目标，是使人们避免或尽量少接触已知的致癌因素和危险因素。根据肝癌的病因学方面的研究，我国在肝癌高发地区采取了“管水、管粮、防肝炎”的战略措施，或者说实行了“防治肝炎、管粮防霉、适量补硒、改良饮水”的一级预防。具体如下：\n1、治水管水、改善饮水卫生\n饮水中有机物污染与肝癌发生有一定关联。研究提示饮用高度污染的地面水，加氯水、高浓度三氯甲烷水使患癌症的危险性增加，这种危险性可能来自饮用水污染中具有相加和协同作用的多种致癌物。又有研究提示饮水和HBV携带状态在肝癌发病上有明显的协同作用。\n目前已查明肝癌高发区饮水中含有多种致癌剂，虽然这些污染水体中的各单个致癌含量甚微，但全部致癌物的浓度经长期少量摄入后可达到致癌的阈值，因此不少学者认为改水、管水、改善饮水卫生可能有助于降低肝癌的发病率。近年来，启东县居民加强饮水管理，大部分居民改饮深井水水质符合卫生标准，调查表明肝癌发病率已大幅度下降。扶绥县结合农田水利建设，全县大面积改良饮用水，绝大部分居民饮用深井水和水利水，收到良好效果。\n2、加强粮油食品防霉去毒\n减少黄曲霉毒素摄入量，阻断或抑制黄曲霉毒素的致癌作用。在肝癌高发地区，肝癌的发生率与粮食霉变，特别是玉米的黄曲霉毒素污染呈正相关系。鉴于粮食霉变环节主要在于田间收获期和收获后的处理期以及储存期，不少学者认为加强这些环节的防霉措施极为重要。另外改变种植习惯，以水稻代替玉米，提倡食用大米，也是减少黄曲霉毒素摄入的方法之一。\n对于已经霉变又不能抛弃的粮油食品也可用挑选霉粒及加工减除法除去一定的毒素。\n3、阻断HBV感染，积极防治肝炎\n乙型肝炎病毒感染是目前严重的公共卫生问题。肝癌高发区，其乙肝病毒携带率也高，80%的肝癌病人均有乙肝病毒感染。在肝癌病人中，发现了乙肝病毒DNA整合到肝细胞的DNA中。因此阻断HBV感染是预防原发肝癌的重要途径，而接种乙肝疫苗是控制乙肝最根本和有效的措施。WHO指出在HBV低流行区应选择性使用疫苗。而在中高流行区，所有婴儿都应接种疫苗，应把乙肝疫苗的应用纳入扩大的计划免疫中去。实践证明，对新生儿，特别是HBsAg阳性及(或)HBeAg阳性母亲的新生儿进行乙肝疫苗接种，免疫效果可靠。在启东市，至1990年底，已接种新生儿41717人，疫苗接种率达98.6%，5岁时抗HBS阳性率达82%，目前已观察到慢性肝炎下降的趋势。接种乙肝疫苗预防肝癌的远期效果有待进一步观察证实。\n4、对肝癌高危人群进行药物预防\n国内外的研究提示，提高硒水平可能有助于降低肝癌的发病率。新西兰在低硒的农场使用亚硒酸钠颗粒施田和丹麦对土地喷硒肥，结果改变了当地贫硒的现象。我国启东县在低硒地区38万人群中进行了预防性试验，通过向农作物喷雾硒肥，结果使玉米和大麦硒水平提高了6倍，居民血硒水平也大大提高。动物实验提示，硒能显著抑制肝炎及癌前病变。硒的防癌作用在早期主要表现为抑制增生灶的形成，在晚期抑制增生灶的癌变。近来中美合作在启东县现场居民中干预实验表明，4年来服硒盐(15mg/kg)和硒酵母制剂，人群肝癌标化发病率由原来的42/10万降至30/10万，对照组发病率未见下降，二者差异显著。实践证明在肝癌高发现场补硒安全可行。显示了硒预防肝癌的价值和意义。\n国内外报道的对肝癌有预防作用的化学性药物还有左旋咪唑、维生素A和维生素C等，我国中药和天然食物丰富，开发这一宝库预防肝癌值得探索，最近研究较多的是绿茶。研究表明：绿茶对黄曲霉毒素B1致大鼠肝癌有明显抑制作用，同时也观察到绿茶提取物可抑制二乙基亚硝胺诱发的大鼠肝癌前期病变。肝癌高发区的流行病学也提示，绿茶可能有一定的预防作用。此外尚发现一些治疗肝炎的中药，如丹参、五味子、香菇多糖、云芝多糖等有拮抗黄曲霉毒素致大鼠肝癌形成的作用。\n5、卫生宣传教育和有关行政法规的实施\n一级预防是针对大规模人群的社会工作，范围广、花费大、阻力大，又难以在短期内显示出效果，执行难度大，因此有计划、有组织、有针对性地实施卫生宣传教育，增加公共的防癌意识，是保证肝癌一级预防措施实行的重要条件，必要时应采取有关行政手段及法规。\n二、肝癌的二级预防\n肝癌的一级预防是重要的，在降低肝癌方面有很大的潜力，但当前仍应强调具有实际效果的Ⅱ级预防。在人群预防中，实施肝癌普查或筛检，早期发现肝癌是二级预防的一个重要方面。\n1、普查的对象：80年代以前，我国的肝癌普查工作曾出现一个很大的矛盾，即关于“耗费与效益”的矛盾。在自然人群中普查，即使是上海这样的肝癌高发区，其检出率也只有14.7/10万，耗资甚巨，收效不高。80年代以来，根据流行病学的调查结果，对肝癌的高危人群作了划分，因此肝癌普查从对自然人群普查转为对高危人群普查，检出率大大提高，很好地解决了耗资与效益的矛盾，这一概念也为广大医务工作者接受。一般认为高危人群指40岁以上，乙肝表面抗原阳性以及慢性肝炎病史5年以上(指5年前曾患肝炎者)，尤其是男性的及有家族史者。\n2、普查的方法：作大规模人群的普查必须采用一个方法简便，灵敏度高和准确可靠的检测方法。甲胎蛋白(AFP)的血凝方法大致符合这一要求。AFP血凝法阳性低限为40µg/L，其假阳性率为30%，对每一例AFP血凝法阳性病例应作放射免疫法复核。AFP确实增高者应建议其到专科诊查。\n我国原发性肝癌患者中AFP检测的阳性率约为70%，即约有近1/3的患者难于以AFP检测获得早期发现。AFP以外的其他肝癌标志物因种种原因皆不适于普查。B超的临床应用已经证实是一种简便易行、准确可靠的影像学诊断方法，近年来已被逐步列入肝癌普查工作中。B超与AFP联合检测确实解决了AFP阴性病例的肝癌早期发现问题。\n3、普查的间隔时间：关于普查的间隔时间，各学者报告基本一致，一般认为对于高危人群，至少每6个月普查一次。\n4、普查工作的组织：应通过各种渠道广泛宣传癌症的防治知识及癌症早期发现的重要性，对高危人群的宣传工作尤应注意既能使其认真对待，定期接受检查，又避免不必要的紧张。\n要做好普查工作必须调动厂矿企业等基层保健组织医务人员的积极性，做好动员及检查对象的组织工作，定期检查对AFP增高病例督促密切随访工作。", "cause": "黄曲霉毒素对大鼠、鸭、豚鼠等动物有强烈的致癌作用。动物实验证明，黄曲霉素B1是肝癌最强的致癌物。流行病学调查发现在一些肝癌高发地区，粮油、食品(如玉米、麦、大豆、花生等)受黄曲霉素B1污染的情况往往比较严重，而在低发区较少见。这些均提示黄曲霉素可能是某些地区肝癌多发的因素，但迄今尚无致人类肝癌的直接证据。最近有报道，流行病学调查黄曲霉毒素与肝癌无关，尚待进一步研究。\n动物实验证明，一些化学物如亚硝胺类和偶氮苯类在很多动物中能引起肝癌。在某些肝癌高发区的土壤及水源中，发现含硝酸盐及亚硝酸盐类物质较高。而亚硝酸盐在胃内酸性条件下可生成亚硝胺，这些化学致癌物与肝癌的关系值得注意和研究。\n中华分支睾吸虫寄生肝内小胆管，刺激胆管上皮细胞增生，有的可发生癌变，成为胆管细胞癌，因在切片中看到由胆管上皮细胞增生逐渐发展到癌的各个阶段，故认为此类肝癌是在寄生虫感染的物理或化学刺激下产生的。但绝大多数胆管细胞癌并无肝吸虫感染，故可能还有其它原因。血吸虫病肝硬化的肝细胞多呈萎缩而无明显增生，因此很少引起肝癌。\n肝癌有时可出现家族聚集现象，多系共同生活并有血缘关系，许多学者认为家族聚集的原因可能系由于病毒性肝炎的母子垂直传播引起。(二)微量元素　从高发区土壤，饮水，粮食，人的头发及血液中分别检测微量元素发现铜、锌较高，钥较低。微量元素铜、锌和肝癌的关系值得注意。(三)营养不良和营养缺乏　营养与肿瘤是90年代人类健康的重大议题，受到社会各界的重视。其作用是在促癌阶段，加速或减慢 ——癌变。高脂及腌、熏食品与肿瘤的发生关系最为密切，宜多吃蔬菜、水果和杂粮。动物实验证实，高脂饮食、低蛋白血症、蛋氨酸及胆硷缺乏，可引起肝细胞坏死、脂肪性变、肝硬变和肝癌。如饲料富于蛋白质，蛋氨酸和B族维生素，则肝癌延迟发生，甚至不发生。\n发病机制\n1.肝癌的大体形态及分类\n肝癌结节外观多数呈球状，边界不甚规则，肿瘤周围可出现“卫星结节”，肝脏周边部靠近包膜的癌结节一般凸出表面但无中心凹陷，癌结节切面多呈灰白色，部分可因脂肪变性或坏死而呈黄色，亦可因含较多胆汁而显绿色，或因出血而呈红褐色，出血坏死多见于大结节的中央部，癌结节质地与组织学类型有关，实体型癌切面呈均质，光滑且柔软;梁状型癌切面则干燥呈颗粒状;胆管细胞癌因富含胶原纤维质地致密，肝癌体积明显增大，重量可达2000～3000g，不伴肝硬化的巨块型肝癌体积更大，重量可达7000g以上，多数肝癌伴大结节性或混合性肝硬化，部分门静脉，肝静脉腔内可见癌栓形成。\n(1)1901年Eggel分型：将肝癌大体分为巨块型，结节型和弥漫型三种类型。\n①巨块型：癌组织呈大块状，可以是单发性，也可以由许多密集的小结节融合而成，一般以肝右叶多见，约占73%，类似膨胀性生长，周围可有假包膜形成，合并肝硬化较轻，手术切除率较高，预后也较好，但有报道伴有“卫星结节”的巨块型肝癌预后差。\n②结节型：肝癌由许多大小不等的结节组成，也可由数个结节融合成大结节，常伴有明显肝硬化，手术切除率低，预后较差。\n③弥漫型：最少见，主要由许多癌结节弥散分布于全肝，伴肝硬化，预后极差，这一传统分型已沿用至今，主要适用于已有临床表现的肝脏较大和较晚期肝癌。\n肉眼观察原发性肝癌既有上述不同类型，其发生之方式因此也有不同解释，有的学者认为肝癌的发生是多中心的，即癌肿是同时或相继地自不同的中心生出;也有人认为癌肿的发生是单中心的，即癌肿初起时仅有一个中心，而肝内的其他结节均为扩散转移的结果，就临床的观点看来，不论肝癌是以何种方式发生，显然结节型及弥散型的肝癌更为严重，因为这种肝癌的恶性程度很高，且病变已经累及肝脏的两叶，故预后最劣。\n(2)奥田邦雄(日本)结合肝癌的生长方式将肝癌分为：\n①膨胀型：癌肿边界清晰并有包膜形成，有单结节或多结节，常伴有肝硬化。\n②浸润型：癌肿边界不清，多数不伴肝硬化。\n③混合型：在膨胀型癌灶外伴有浸润型肝癌存在，同样分为单结节型和多结节型。\n④弥漫型：肝脏弥散性的小结节癌灶，结节直径多在1cm以下，分布于整个肝脏。\n⑤特殊型：如带蒂外生型，肝内门静脉癌栓而无实质癌块等，不同地区肝癌的病理表现不同，如日本以膨胀型为多，北美以浸润型为多，南非的肝癌常不伴有肝硬化。\n(3)我国目前应用的肝癌大体分类标准：全国肝癌病理协作组在Eggel分类基础上又提出以下分型即弥漫型，块状型(包括单块状，融合块状，多块状)，结节型(包括单结节，融合结节和多结节)，小癌型。\n①弥漫型：癌结节小，呈弥散性分布，此型易与肝硬化混淆。\n②块状型：癌肿直径>5cm，其中>10cm者为巨块型，可在分为3个亚型。\nA.单块型：单个癌块，边界较清楚或不规则，常有包膜。\nB.融合型：相邻癌肿融合成块，周围肝组织中有散在分布的卫星癌结节。\nC.多块型：由多个单块或融合块癌肿形成。\n③结节型：癌结节直径>5cm，可再分为3个亚型：\nA.单结节型：单个癌结节，边界清楚有包膜，周边常见小的卫星结节。\nB.融合结节型：边界不规则，周围散在卫星结节。\nC.多结节型：分散于肝脏各处，边界清楚或不规则。\n④小癌型：单个癌结节直径≤3cm，或相邻两个癌结节直径之和≤3cm，边界清楚，常有明显包膜。\n2.组织学分型\n根据肝癌的组织学来源，将其分为3型：\n(1)肝细胞癌：最多见，多数伴有肝硬化，一般相信系由实质细胞产生，占肝癌病例之90%～95%(我国占91.5%)，主要见于男性，癌细胞呈多角形，核大而且核仁明显，胞浆呈颗粒状，为嗜酸性，排列成索状或巢状，尤以后者为多见，有时在分化较好的癌细胞中可见到胆汁小滴，癌巢间有丰富的血窦，癌细胞有向血窦内生长的趋势(图1)，肝细胞癌分为索状/梁状型，索状腺样型，实体型和硬化型四种类型，同一病例中有时可见结节性增生，腺瘤和肝癌等不同病变同时存在，且常伴有肝硬化。\n(2)胆管细胞癌：女性多见，约占女性肝癌的30.8%，根据其来源可分为两种，一种来自小胆管，癌细胞较小，胞浆较清晰，形成大小不一的腺腔，间质多而血窦少，这一类在临床相对多见，另一种来自大胆管上皮，癌细胞较大，常为柱状，往往形成较大的腺腔，这一类较少见，胆管细胞癌不分泌胆汁而是分泌黏液(图2)，胆管细胞癌根据形态一般分为管状腺癌，鳞腺癌，乳头状腺癌三种亚型，与肝细胞癌相比，胆管细胞癌往往无肝病背景，极少伴有肝硬化，癌块质硬而无包膜，结缔组织较多，以淋巴道转移为主，临床表现为早期出现黄疸，发热，门脉高压症状少见，仅约20%患者AFP轻度增高。\n(3)混合型：较少见，其特点是部分组织形态似肝癌细胞，部分似胆管癌细胞，两种细胞成分有的彼此分隔，有的混杂，界线不清，混合型肝癌可分为分离型，过渡型，混杂型三种亚型。\n(4)超微结构：肝癌细胞超微结构特点有：\n①细胞大，形态不规则，血管壁有基底膜，Disse间隙充以胶质纤维，血窦内皮细胞可能缺如，癌细胞直接与血液接触，毛细胆管少，结构不清，管侧细胞间隙不规则增宽，相对的细胞膜有大小不一的微绒毛，上述增宽的间隙可与Disse间隙或血窦相连；\n②细胞器数量和类型与肝癌分化有关，高分化的癌细胞保留线粒体，有较多扩张的粗面内质网，核糖体较多，有时光面内质网呈螺纹状，称“指印”或“髓鞘”，分化低的癌细胞细胞器减少，线粒体大而异形，稀少，有时有包涵体，整个细胞显得单调；\n③细胞核大，不规则，可内陷，黏膜粗糙，核周间隙扩张，甚至形成囊泡，核仁多，大且不规则。\n相对特征的亚微变化：\n①假包涵体；胞核不规则内陷，形成囊袋或分叶状，其中包罗含细胞器的胞浆；\n②髓样小体：由次级溶酶体中残留的线粒体或内质网形成的同心圆结构。\n此外，在肝癌细胞中能发现一些特殊物质：\n①糖原颗粒；\n②脂滴；\n③AFP在粗面内质网集中处；\n④HBsAg位于光面内质网，HBcAg位于细胞核，HCV样颗粒位于核内。\n3.肝细胞癌的分级\n国内外对原发性肝癌曾有过各种不同的临床分型方法，如Berman将其分为显著癌肿型，急腹症型，发热型，隐匿型和转移型，以显著癌肿型占多数，国内钟学礼等将其归纳为10型，即肝肿大型，肝脓肿型，肝硬化型，阻塞性黄疸型，腹腔出血型，血糖过低型，胆囊炎与胆石症型，慢性肝炎型，腹内囊肿型及弥漫性癌肿型;林兆耆等又增加了类白血病型及截瘫型，共12型，上述这些分型方法都是根据中，晚期肝癌患者的临床表现加以区分的，而对无临床症状的早期患者均不适用，因此，由于原发性肝癌临床表现的多样化，临床上对这些患者均应加以详细询问病史及体格检查，特别对患过肝病的患者尤须提高警惕。\n根据癌细胞的分化程度，将肝细胞癌分为Ⅰ，Ⅱ，Ⅲ，Ⅳ四级，其中Ⅰ级为高分化型，Ⅱ，Ⅲ级为中分化型，Ⅳ级为低分化型，以中分化型肝细胞癌最多见。\nⅠ级：癌细胞形态与正常肝细胞相似，一般呈索条状排列，胞浆呈嗜酸性，核圆，大小较规则，核分裂少见。\nⅡ级：癌细胞形态轻度变形，呈索条状或巢状排列，核浆比例明显增大，胞浆轻度嗜碱性，常可见到胆汁小滴，核分裂增多。\nⅢ级：癌细胞明显变形，呈巢状排列，核浆比例增大，胞浆染色呈嗜酸性，胆汁小滴少见，核的大小，染色不规则，核分裂多见，有时见癌巨细胞。\nⅣ级：癌细胞呈明显异形，可见到梭形细胞和多核巨细胞，胞浆少而核深染，核分裂多，细胞排列紊乱，常无胆汁小滴。\n4.肝细胞癌的TNM分期\nUICC 1987年关于原发性肝癌的TNM分类如下：\nTx原发肿瘤不明，T0无原发癌证据。\nT1：单个结节≤2cm，无血管侵犯。\nT2：单个结节≤2cm，侵犯血管，或多个局限一叶，≤2cm，未侵犯血管;或单个，>2cm，未侵犯血管。\nT3：单个结节，>2cm，侵犯血管;或多个，局限于一叶，≤2cm，侵犯血管;或多个，一叶内，>2cm，伴或不伴血管侵犯。\nT4：多个结节，超出一叶;或侵犯门静脉主支或肝静脉。\nN0：局部淋巴结无转移。\nN1：有局部淋巴结转移。\nM0：无远处转移。\nMl：有远处转移。\n日本在TNM分类基础上将肝癌分为4期，Ⅰ期为T1N1M0;Ⅱ期为T2N0M0;Ⅲ期为T3N0M0或T1～3N1M0;Ⅳa期为T4N0～1M0，Ⅳb期为T1～4N0Ml。\n研究表明，Ⅰ，Ⅱ，Ⅲ，Ⅳa，Ⅳb期手术切除率分别为100%，82.7%，76.3%，51.4%和50.0%;根治性切除率为88.9%，60.2%，32.6%，7.6%和6.3%;治疗后三年生存率分别为Ⅰ期88.2%，Ⅱ期60.0%，Ⅲ期28.0%，Ⅳa期12.1%。\n5.特殊类型的肝癌\n(1)纤维板层型肝癌：纤维板层型肝癌(fibrolamemellar carcinoma of liver)是近年发现和认识的一种特殊类型的肝细胞癌，具有许多不同于HCC的特点：\n①多见于青年；\n②少有HBY感染背景；\n③少伴有肝硬化；\n④AFP常呈阴性；\n⑤瘤灶常为单发；\n⑥肿瘤生长缓慢；\n⑦手术切除率高；\n⑧不论切除与否预后均较好，中位生存期HCC为6个月，而纤维板层型肝癌可达32～68个月;获手术切除的HCC中位生存期22个月，纤维板层型肝癌达50个月，纤维板层型肝癌的病理诊断标准为：\n①强嗜酸性颗粒状的癌细胞浆；\n②在癌细胞巢间有大量平行排列的板层状纤维基质，此型肝癌在西方国家肝癌中所占比例较高，而我国，日本，非洲等地则少见，新近发现其胶原基质主要含胶原Ⅰ，Ⅲ，Ⅴ，癌细胞常表达转化生长因子β1(TGF-β1)，而基质细胞则表达白细胞介素6(IL-6)，这些细胞因子的过量表达可能与胶原基因表达的改变有关。\n(2)小肝癌：单个癌结节直径或相邻两个癌结节直径之和小于3cm的肝癌称为小肝癌，与大肝癌比较，小肝癌在病理上具有的特点：\n①常为单个结节，有报道小肝癌中仅3%伴有卫星结节，卫星结节的发生率常与肿瘤大小呈正相关；\n②常形成包膜，尤其以膨胀性生长为主，如肿瘤小于1cm，则包膜常未形成，因为肝癌包膜常在肿块直径约1.5cm时形成;呈浸润性生长为主，则肿瘤边界不规则且常无包膜形成；\n③分化程度较好，多为Ed-mondson Ⅰ～Ⅱ级，癌细胞的分化程度常与肿块大小呈正相关，随着肿块的增大，恶性程度逐渐增高；\n④流式细胞仪提示小肝癌DNA常为二倍体，随着体积的增大而向多倍体发展；\n⑤小肝癌经手术切除后患者的预后明显优于非手术者，小肝癌手术切除后一，二，三，四年生存率分别为75%，46.7%，45.5%和40%，而大肝癌则为34.9%，32.1%，15.8%和7.7%；\n⑥小肝癌细胞形态属肝癌细胞类型，细胞形态及分化程度极为一致，而且出血坏死极少；\n⑦肉眼少见血管内癌栓形成，但镜下血管内癌栓常见，最多见为门静脉腔内漂浮着小簇的肝癌细胞。\n6.肝癌的肝病背景\n我国肝癌常合并有肝硬化，据资料报道，HCC伴肝硬化高达84.65%，肝硬化合并肝癌约49.9%;其中大结节性肝硬化伴肝癌的发生率高达73%，小结节性肝硬化伴肝癌的发生率为34.1%，故有人将大结节性肝硬化称为肝癌有关的肝硬化，这类肝硬化多来自肝炎后肝硬化。\n肝癌常有HBV感染的背景，据统计学调查发现，在我国90%的肝癌患者有HBV感染背景，10%有HCV感染史。\n7.肝癌癌前病变\n癌前病变是指一类具有癌变倾向，但不一定演变成癌的病变，目前肝癌的癌前病变有肝细胞不典型增生(DLC)，腺瘤样增生和肝硬化。\n肿瘤的发生一般经过启动，促进和演进三个阶段，在大鼠实验性肝癌发生过程中发现，肝细胞在外界致癌因素作用下发生基因突变，此时处于肝癌的启动阶段，肝癌相关基因中发生诸如IGF-Ⅱ等早期基因异常激活和过量表达，在致癌因素的持续作用下，这类细胞发展成为单细胞克隆，不断繁殖，此时为癌前期病变，但基因表达基本稳定，处于促进阶段;随后癌前期病变细胞表现为细胞核不稳定性，逐渐形成增生灶，细胞过量表达如G-myc等原癌基因蛋白，即为演进期，进而发展为肝癌。\n(1)肝细胞不典型增生：DLC与正常细胞比较，体积明显增大，约为正常肝细胞的2～3倍，排列紧密，形成的细胞索较厚，胞浆丰富，胞核大且略不规则，苏木素染色深，核膜厚，染色质分布不均匀，核仁大而明显，有时出现双核，应用流式细胞仪，扫描显微分光光度仪，图像分析技术等测定细胞内DNA含量，染色原倍体分析，核面积，核不规则指数等也发现DLC趋同于肝癌细胞，基因表达产物分析发现，DLC中GTP酶，ATP酶明显减少或消失，癌基因产物ras，myc，IGF-Ⅱ等较正常肝细胞明显增加，与肝癌细胞相比较，DLC胞浆嗜伊红，核浆比例接近正常，无核分裂象，核仁组成区银染蛋白多属正常范围。\nWatanabe将DLC分为大细胞性和小细胞性两类，小细胞性不典型增生更趋于癌前病变，其特点主要为：\n①胞浆减少；\n②胞体小于正常肝细胞；\n③核中度增大，核/浆比例增大。\n化学诱癌的动物实验中发现，肝汇管区存在一种卵圆细胞，该细胞是一种干细胞，具有多向分化潜能，在正常情况下，可向肝细胞和胆管上皮细胞转化，在致癌因素作用下可转化成多种类型的癌细胞，用化学致癌物刺激卵圆细胞，并转导ras基因，然后将其接种于小鼠，可诱导发生复合癌，肝癌，胆管细胞癌，上皮-间皮混合瘤等多种类型肿瘤，证明了卵圆细胞的分化潜能，在人癌旁肝组织和慢性活动性肝炎组织中已发现类似形态的卵圆细胞，但其转归或转化机制如何，尚待进一步研究。\n(2)肝硬化：许多研究提示肝硬化与肝癌的发生关系密切，流行病学资料显示，在我国约40%肝硬化合并肝癌，而肝癌合并肝硬化高达85%，尤其是大结节性肝硬化合并肝癌高达73%，绝大多数肝癌是在大结节性肝硬化基础上发生，发展而来，从分子基础来看，肝硬化与肝癌有一定程度的一致性，癌旁硬变的肝组织中IGF-Ⅰ，IGF-Ⅱ及其受体的表达水平明显增高，其他如C-myc，N-ras，ets-2等基因过表达与肝癌细胞相似，而不同于正常肝细胞，病理研究证明，在肝硬化假小叶内发现不典型增生肝细胞的频率很高，有可能肝硬化发生肝癌转化的过程就是由DLC恶性演化而形成。\n(3)腺瘤样增生：腺瘤样增生的病理特征是肝脏呈弥漫性结节性改变，肝脏可以正常，增大或缩小，应用化学致癌剂如AFB1，二乙基亚硝胺诱癌时，肝脏可出现腺瘤样增生改变，在腺瘤样增生肝组织中，可以发现不典型增生肝细胞，对腺瘤样增生患者的追踪调查证明，部分患者可以发展为肝癌。\n8.肝癌的恶性生物学特征\n肝癌细胞生长活跃，侵袭性强，周围血窦丰富，极易侵袭包膜和血管，导致局部扩散和远处转移，肝癌转移的发生率与疾病的病程发展，肿瘤的生物学特性以及机体的免疫功能等因素密切相关，有肝内转移和肝外转移，转移的途径有血行播散，淋巴道转移，直接浸润和种植转移，医源性转移多与手术操作有关，肝癌破裂可导致腹腔内广泛转移，许多病例发现早期就可以通过门静脉癌栓转移至肝脏或其他脏器，小肝癌的血管内癌栓形成率达30%，所以肝内转移是肝癌最常见的转移途径，尸检发现，肝外癌转移亦不少见，转移率约达40%～71.6%。\n(1)肝癌的转移途径：肝癌的转移可通过血道，淋巴道和直接播散，局部扩散等方式转移到其他器官或组织。\n①血道转移：肝癌侵入门静脉导致肝内血道转移十分常见，在血窦丰富，纤维组织稀少，无肝硬化的肝组织中更为明显，故常形成多个“卫星结节”，肝癌经血道肝外转移的主要脏器为肺脏，肝癌发生肺转移约占肝外转移的90%，多因血管中小癌栓进入血液循环后滞留肺脏形成转移癌灶，肺内癌转移结节直径<1cm，弥散分布于肺叶，常呈球状，切面呈灰白色，中央可有出血，坏死，肝癌骨转移亦较常见，各地报道的资料不一致，在3%～16.2%，常见部位为脊椎骨，肋骨和胸骨，其次为骨盆，头骨和股骨上端，骨转移癌可导致病理性骨折，少数肝癌可以转移到肾上腺，肾和脑。\n②淋巴道转移：大约30%肝癌细胞和70%胆管癌细胞是经淋巴道转移，多数首先转移至肝门淋巴结，少数也可以转移到胰周，腹主动脉旁，腹膜后，纵隔及锁骨上淋巴结。\n③播散转移：一般出现在肝癌晚期，特别是生长在接近肝脏表面部位的肝癌，往往先破坏肝包膜，继之发生种植性转移，最常见的是腹膜转移。\n④局部扩散：肝癌细胞可以直接侵袭和浸润周围肝包膜，近肝被膜的癌结节亦可浸润邻近器官和组织，如横膈，胃，结肠，右侧胸腔等。\n(2)影响肝癌转移的因素甚多，主要有：\n①病人年龄：30岁以下转移多见，且发生早而广泛。\n②肝癌细胞的分化程度和侵袭性：一般分化程度低者容易发生转移。\n③是否合并肝硬化：合并肝硬化患者易发生转移，转移率达84%，而不合并肝硬化者转移率为60%。\n近年从分子水平分析发现，呈侵袭性生长的肝癌中67%MMP-2mRNA表达明显增高，MMP-2亦呈不同程度的阳性表达;而包膜完整的肝癌细胞仅有20%MMP-2mRNA表达，30%MMP-2表达阳性;已发生门静脉癌栓或转移的肝癌MMP-2阳性率(83.3%)明显高于未转移肝癌(37.5%)(P<0.01)，伴肝内转移的癌组织微血管密度(MDV)，PCNA明显高于不伴肝内转移者，此外肝癌细胞nm23，MDV，MMP-2，PCNA的表达水平与肝癌的转移有关，可作为病程进展，治疗方式选择及预后判断的参考指标。", "symptom": ["腹水", "胸痛", "红细胞增多", "恶病质", "呕血", "门脉高压", "纳差", "钝痛", "内出血", "低血磷", "高钙血症", "上腹部疼痛", "腹胀", "食欲减退", "淋巴结肿大", "硬化", "脑转移", "血管杂音", "消化性溃疡", "骨转移", "胸腔积液", "组织坏死", "体重减轻", "乏力", "蜘蛛痣", "低血糖症", "阻塞性黄疸", "呕吐", "黄疸", "黑便", "昏迷", "鼻出血", "消瘦", "肝功能受损", "下肢水肿", "溃疡", "低热", "消化不良", "胀痛", "高热", "出血倾向", "血性腹水", "腹痛", "囊肿", "脓肿", "血小板增多", "截瘫", "剧痛", "贫血", "恶心", "寒战", "类癌综合征", "结节", "肝掌", "脾功能亢进", "腹部肿块", "静脉曲张", "水肿", "腹泻", "肝脏肿大", "咯血", "脾大", "甲状旁腺功能亢进", "休克", "肝大", "嗜睡"], "yibao_status": "否", "get_prob": "2%", "easy_get": "本病可发生于任何年龄，以40～49岁最多，男女之比为2～5∶1。", "get_way": "无传染性", "acompany": ["消化道出血"], "cure_department": ["肿瘤科", "中医肿瘤科"], "cure_way": ["手术治疗", "药物治疗", "支持性治疗"], "cure_lasttime": "需要终身治疗", "cured_prob": "30%", "common_drug": ["复方万年青胶囊", "康莱特注射液"], "cost_money": "根据不同医院，收费标准不一致，市三甲医院约（50000——100000元）", "check": ["血清γ-谷氨酰转肽酶同工酶", "血清碱性磷酸酶同工酶", "胎甲球（a-FA/AFP)", "5＇-核苷酸磷酸二酯酶同工酶", "甘氨酰脯氨酸二肽氨基肽酶", "苷-胆酸", "铜蓝蛋白", "血红素结合蛋白", "血清5"-核苷酸酶（5"-NT）", "血清α-L-岩藻糖苷酶"], "do_eat": ["鸡蛋", "葵花子仁", "白果（干）", "青豆"], "not_eat": ["干腌菜", "啤酒", "白酒", "咸鸭蛋"], "recommand_eat": ["枸杞甲鱼", "茯苓清蒸桂鱼", "翠衣番茄豆腐汤", "萝卜丝包", "萝卜丝拌豆芽", "山药牛蒡汁", "赤小豆山药粥"], "recommand_drug": ["去甲斑蝥素片", "肝复乐胶囊", "艾迪注射液", "楼莲胶囊", "散结片", "安替可胶囊", "养正消积胶囊", "复方氟尿嘧啶口服溶液", "复方万年青胶囊", "康莱特注射液", "注射用盐酸表柔比星", "葫芦素片", "槐耳颗粒", "金龙胶囊", "复方斑蝥胶囊", "慈丹胶囊", "蛇莲胶囊"], "drug_detail": ["天力泰药业复方万年青胶囊(复方万年青胶囊)", "康莱特康莱特注射液(康莱特注射液)", "吉尔吉药业蛇莲胶囊(蛇莲胶囊)", "建生药业金龙胶囊(金龙胶囊)", "今方药业散结片(散结片)", "以岭药业养正消积胶囊(养正消积胶囊)", "华北制药去甲斑蝥素片(去甲斑蝥素片)", "仁仁复方斑蝥胶囊(复方斑蝥胶囊)", "勃然制药慈丹胶囊(慈丹胶囊)", "康普药业肝复乐胶囊(肝复乐胶囊)", "三顺制药复方氟尿嘧啶口服溶(复方氟尿嘧啶口服溶液)", "山东信谊去甲斑蝥素片(去甲斑蝥素片)", "益佰制药艾迪注射液(艾迪注射液)", "远大国奥安替可胶囊(安替可胶囊)", "迪诺制药葫芦素片(葫芦素片)", "天津药物研究院葫芦素片(葫芦素片)", "方舟制药复方斑蝥胶囊(复方斑蝥胶囊)", "通化万通楼莲胶囊(楼莲胶囊)", "盖天力槐耳颗粒(槐耳颗粒)", "黄河中药复方斑蝥胶囊(复方斑蝥胶囊)", "华西制药复方斑蝥胶囊(复方斑蝥胶囊)", "去甲斑蝥素片(去甲斑蝥素片)", "艾达生(注射用盐酸表柔比星)"]}
